In [ ]:
import boto3, uuid, itertools
from datetime import datetime

session = boto3.Session(profile_name='slscode')
ddb_client = session.client('dynamodb')
ddb_resource = session.resource('dynamodb')

In [ ]:
table_definition = dict(
    AttributeDefinitions=[
        {
            'AttributeName': 'user',
            'AttributeType': 'S'
        },
        {
            'AttributeName': 'event_ts',
            'AttributeType': 'N'
        },
        {
            'AttributeName': 'event_id',
            'AttributeType': 'S'
        },
    ],
    TableName='test-ddb-table',
    KeySchema=[
        {
            'AttributeName': 'user',
            'KeyType': 'HASH'
        },
        {
            'AttributeName': 'event_id',
            'KeyType': 'RANGE'
        },
    ],
    LocalSecondaryIndexes=[
        {
            'IndexName': 'user_by_ts',
            'KeySchema': [
                {
                    'AttributeName': 'user',
                    'KeyType': 'HASH'
                },
                {
                    'AttributeName': 'event_ts',
                    'KeyType': 'RANGE'
                },
            ],
            'Projection': {
                'ProjectionType': 'INCLUDE',
                'NonKeyAttributes': [
                    'event_id'
                ]
            }
        },
    ],
    #GlobalSecondaryIndexes=[],
    ProvisionedThroughput={
        'ReadCapacityUnits': 2,
        'WriteCapacityUnits': 2
    },
    StreamSpecification={
        'StreamEnabled': False,
        #'StreamViewType': 'NEW_AND_OLD_IMAGES'
    }
)

In [ ]:
from botocore import exceptions as botocore_errors
from boto3 import exceptions as boto3_errors

In [ ]:
try:
    response = ddb_client.create_table(**table_definition)
except botocore_errors.ClientError as exc:
    if 'ResourceInUseException' in str(exc):
        print("Table exists, skipping creation")
    else:
        raise
else:
    print(response)

In [ ]:
#ddb_client.delete_table(TableName='test-ddb-table')

In [ ]:
table = ddb_resource.Table('test-ddb-table')
from datetime import datetime
with table.batch_writer() as batch:
    for user, ts in zip(itertools.cycle(['joe', 'jane', 'alex']), range(0, 10000, 100)):
        batch.put_item(Item={
            'user': user,
            'event_ts': int(ts + datetime.utcnow().timestamp()),
            'event_id': uuid.uuid4().hex,
            'extradata': 'foobar',
            'batched': True
        })

In [ ]:
resp = table.scan()
resp

In [ ]:
len(resp['Items'])

In [ ]:
resp['ResponseMetadata']

In [ ]:
q_resp = table.query(IndexName='user_by_ts',
    KeyConditionExpression='#U = :target_user',
    ExpressionAttributeValues={':target_user': 'alex'},
    ExpressionAttributeNames={'#U': 'user'}
)
q_resp

In [ ]:
q_resp['Items'][0]